In [113]:
import pandas as pd
import numpy as np
from gensim.models import Word2Vec,FastText
import re
from sklearn.decomposition import PCA
from matplotlib import pyplot as plt 
from sklearn.model_selection import train_test_split

# import ploty.graph_objects as go
import warnings 
warnings.filterwarnings('ignore')

In [114]:
train_df=pd.read_csv("train_E6oV3lV.csv")
test_df=pd.read_csv("test_tweets_anuFYb8.csv")

In [115]:
train_df.shape

(31962, 3)

In [116]:
test_df.shape

(17197, 2)

In [117]:
train_df.head()

id  label                                              tweet
0   1      0   @user when a father is dysfunctional and is s...
1   2      0  @user @user thanks for #lyft credit i can't us...
2   3      0                                bihday your majesty
3   4      0  #model   i love u take with u all the time in ...
4   5      0             factsguide: society now    #motivation

In [118]:
test_df.head()

id                                              tweet
0  31963  #studiolife #aislife #requires #passion #dedic...
1  31964   @user #white #supremacists want everyone to s...
2  31965  safe ways to heal your #acne!!    #altwaystohe...
3  31966  is the hp and the cursed child book up for res...
4  31967    3rd #bihday to my amazing, hilarious #nephew...

In [119]:
train_df["label"].value_counts()

0    29720
1     2242
Name: label, dtype: int64

In [120]:
combine_df=train_df.append(test_df,ignore_index=True)

In [121]:
combine_df.head()

id  label                                              tweet
0   1    0.0   @user when a father is dysfunctional and is s...
1   2    0.0  @user @user thanks for #lyft credit i can't us...
2   3    0.0                                bihday your majesty
3   4    0.0  #model   i love u take with u all the time in ...
4   5    0.0             factsguide: society now    #motivation

In [122]:
combine_df.shape

(49159, 3)

In [123]:
combine_df.tail()

id  label                                              tweet
49154  49155    NaN  thought factory: left-right polarisation! #tru...
49155  49156    NaN  feeling like a mermaid ð #hairflip #neverre...
49156  49157    NaN  #hillary #campaigned today in #ohio((omg)) &am...
49157  49158    NaN  happy, at work conference: right mindset leads...
49158  49159    NaN  my   song "so glad" free download!  #shoegaze ...

In [124]:
def remove_pattern(input_txt, pattern):
    r = re.findall(pattern, input_txt)
    for i in r:
        input_txt = re.sub(i, '', input_txt)
        
    return input_txt

In [125]:
combine_df['clean_tweet']= np.vectorize(remove_pattern)(combine_df['tweet'], "@[\w]*")

In [126]:
combine_df.head()

id  label                                              tweet  \
0   1    0.0   @user when a father is dysfunctional and is s...   
1   2    0.0  @user @user thanks for #lyft credit i can't us...   
2   3    0.0                                bihday your majesty   
3   4    0.0  #model   i love u take with u all the time in ...   
4   5    0.0             factsguide: society now    #motivation   

                                         clean_tweet  
0    when a father is dysfunctional and is so sel...  
1    thanks for #lyft credit i can't use cause th...  
2                                bihday your majesty  
3  #model   i love u take with u all the time in ...  
4             factsguide: society now    #motivation

In [127]:
combine_df['clean_tweet']= combine_df['clean_tweet'].str.replace("[^a-zA-Z#]", " ")
combine_df.head(15)

id  label                                              tweet  \
0    1    0.0   @user when a father is dysfunctional and is s...   
1    2    0.0  @user @user thanks for #lyft credit i can't us...   
2    3    0.0                                bihday your majesty   
3    4    0.0  #model   i love u take with u all the time in ...   
4    5    0.0             factsguide: society now    #motivation   
5    6    0.0  [2/2] huge fan fare and big talking before the...   
6    7    0.0   @user camping tomorrow @user @user @user @use...   
7    8    0.0  the next school year is the year for exams.ð...   
8    9    0.0  we won!!! love the land!!! #allin #cavs #champ...   
9   10    0.0   @user @user welcome here !  i'm   it's so #gr...   
10  11    0.0   â #ireland consumer price index (mom) climb...   
11  12    0.0  we are so selfish. #orlando #standwithorlando ...   
12  13    0.0  i get to see my daddy today!!   #80days #getti...   
13  14    1.0  @user #cnn calls #michigan middle school 'buil...   
14  15    1.0  no comment!  in #australia   #opkillingbay #se...   

                                          clean_tweet  
0     when a father is dysfunctional and is so sel...  
1     thanks for #lyft credit i can t use cause th...  
2                                 bihday your majesty  
3   #model   i love u take with u all the time in ...  
4              factsguide  society now    #motivation  
5         huge fan fare and big talking before the...  
6                    camping tomorrow        danny     
7   the next school year is the year for exams    ...  
8   we won    love the land    #allin #cavs #champ...  
9               welcome here    i m   it s so #gr      
10       #ireland consumer price index  mom  climb...  
11  we are so selfish  #orlando #standwithorlando ...  
12  i get to see my daddy today     #  days #getti...  
13   #cnn calls #michigan middle school  build the...  
14  no comment   in #australia   #opkillingbay #se...

In [128]:
combine_df['clean_tweet']= combine_df['clean_tweet'].apply(lambda x: ' '.join([w for w in x.split() if len(w)>3]))

In [129]:
combine_df['clean_tweet'][0]

'when father dysfunctional selfish drags kids into dysfunction #run'

In [130]:
tokenized_tweet = combine_df['clean_tweet'].apply(lambda x: x.split())

In [131]:
tokenized_tweet.head()

0    [when, father, dysfunctional, selfish, drags, ...
1    [thanks, #lyft, credit, cause, they, offer, wh...
2                              [bihday, your, majesty]
3                     [#model, love, take, with, time]
4                   [factsguide, society, #motivation]
Name: clean_tweet, dtype: object

In [132]:
from nltk.stem.porter import *
stemmer = PorterStemmer()

tokenized_tweet = tokenized_tweet.apply(lambda x: [stemmer.stem(i) for i in x]) # stemming
stemmer.stem("runs")

'run'

In [133]:
stemmer.stem("playing")

'play'

In [134]:
tokenized_tweet.head()

0    [when, father, dysfunct, selfish, drag, kid, i...
1    [thank, #lyft, credit, caus, they, offer, whee...
2                              [bihday, your, majesti]
3                     [#model, love, take, with, time]
4                         [factsguid, societi, #motiv]
Name: clean_tweet, dtype: object

In [135]:
for i in range(len(tokenized_tweet)):
    tokenized_tweet[i] = ' '.join(tokenized_tweet[i])
    
combine_df['clean_tweet'] = tokenized_tweet

In [136]:
combine_df['clean_tweet'].head()

0    when father dysfunct selfish drag kid into dys...
1    thank #lyft credit caus they offer wheelchair ...
2                                  bihday your majesti
3                           #model love take with time
4                             factsguid societi #motiv
Name: clean_tweet, dtype: object

In [137]:
tokenized_tweet = combine_df['clean_tweet'].apply(lambda x: x.split()) # tokenizing

model_w2v = Word2Vec(tokenized_tweet,  vector_size=200,window=5)

model_w2v.train(tokenized_tweet, total_examples= len(combine_df['clean_tweet']), epochs=20)

model_w2v.wv.most_similar(positive="dess")

[('#dinner', 0.8153944611549377),
 ('#pancak', 0.8138015270233154),
 ('#italian', 0.7993360757827759),
 ('#delici', 0.7805869579315186),
 ('#ride', 0.7788397073745728),
 ('#iftar', 0.778695821762085),
 ('#tea', 0.7753797173500061),
 ('#lunch', 0.7748924493789673),
 ('#lunchtim', 0.771467924118042),
 ('#bestday', 0.7644183039665222)]

In [138]:
model_w2v.wv.most_similar(positive="credit")

[('payment', 0.6509057879447937),
 ('intellig', 0.6145698428153992),
 ('higher', 0.6128914952278137),
 ('zero', 0.5998456478118896),
 ('impress', 0.5882589221000671),
 ('mcdonald', 0.5862919092178345),
 ('foreign', 0.5754274725914001),
 ('paper', 0.5720123648643494),
 ('assist', 0.5716372728347778),
 ('classi', 0.5709843635559082)]

In [139]:
def word_vector(tokens, size):
    vec = np.zeros(size).reshape((1, size))
    
    count = 0.
    for word in tokens:
        print(word)
        try:
            vec += model_w2v.wv[word].reshape((1, size))
            count += 1.
        except KeyError: # handling the case where the token is not in vocabulary
                         
            continue
    if count != 0:
        vec /= count
    return vec

In [140]:
wordvec_arrays = np.zeros((len(tokenized_tweet), 200))

for i in range(len(tokenized_tweet)):
    wordvec_arrays[i,:] = word_vector(tokenized_tweet[i], 200)
    
wordvec_df = pd.DataFrame(wordvec_arrays)
wordvec_df.shape

when
father
dysfunct
selfish
drag
kid
into
dysfunct
#run
thank
#lyft
credit
caus
they
offer
wheelchair
van
#disapoint
#getthank
bihday
your
majesti
#model
love
take
with
time
factsguid
societi
#motiv
huge
fare
talk
befor
they
leav
chao
disput
when
they
there
#allshowandnogo
camp
tomorrow
danni
next
school
year
year
exam
think
about
that
#school
#exam
#hate
#imagin
#actorslif
#revolutionschool
#girl
love
land
#allin
#cav
#champion
#cleveland
#clevelandcavali
welcom
here
#ireland
consum
price
index
climb
from
previou
#blog
#silver
#gold
#forex
selfish
#orlando
#standwithorlando
#pulseshoot
#orlandoshoot
#biggerproblem
#selfish
#heabreak
#valu
#love
daddi
today
day
#gettingf
#cnn
call
#michigan
middl
school
build
wall
chant
#tcot
comment
#australia
#opkillingbay
#seashepherd
#helpcovedolphin
#thecov
#helpcovedolphin
ouch
junior
angri
#got
#junior
#yugyoem
#omg
thank
have
paner
#thank
#posit
retweet
agre
#friday
smile
around
user
#cooki
make
peopl
know
essenti
oil
made
chemic
#euro
peopl
b

minut
lose
sixti
second
#happi
should
same
#sanjapan
#animeconvent
guy
septemb
question
excit
moto
#tech
#announc
#moto
#question
make
today
count
#mondaymotiv
#livelifetothefullest
#healthi
#everydaycount
happi
morn
degre
with
anna
#classmat
#friend
would
abl
suppo
event
#brentwood
#homesta
they
lost
fund
have
close
happi
littl
peopl
happyhappi
peopl
#kitten
#cat
#blackkitten
thank
veri
much
thi
oppoun
will
cherish
forev
themeowood
puppi
more
day
till
happi
pharrel
william
#pharrellwilliam
lyric
happi
confer
right
mindset
lead
cultur
develop
organ
#work
lost
anoth
member
famili
yesterday
#gut
#rosi
yayyy
trailer
morrow
#fever
super
watch
fanci
tail
vine
#mad
#teeth
#bite
#piss
#dog
#bite
#dogbit
#dogtreat
#dreamcatch
bull
will
domin
your
bull
will
direct
whatev
want
when
readi
tomorrow
#englishteach
#teacher
#ecuador
memori
wonder
alway
miss
etern
love
#strong
#greatquot
dalla
shoot
video
about
disturb
viewer
discret
then
they
play
loop
#itako#alone#it
fine
littl
sunshin
sticker
kind


#ilovemysist
els
plan
watch
tomorrow
#usn
rifl
snow
closest
ever
#navi
euro
pundit
make
their
predict
franc
#euro
today
becaus
happi
#happi
#minion
elder
scroll
mani
year
#bethesda
poor
#tiggi
littl
cheeki
#jax
#soa
#throwbackthursday
cannot
wait
#eurogam
thi
year
#pump
#eurogam
veri
work
with
russel
beckwith
soon
#staytun
friend
lyle
#tapfoag
nazi
studi
american
race
law
inspir
#ushistori
#eugen
share
cream
#sun
#love
#outdoor
#picnic
#summer
#famili
#daughter
#father
#dess
#icecream
noth
like
river
island
sale
shop
spree
cheer
#retailtherapi
#riverisland
#shoppingqueen
#alwayscheersyouup
clean
hous
zo
laundri
final
free
from
fever
cold
happi
#clean
#laundryday
list
#ebay
#woohoo
#sell
#sell
#buy
#shop
#shop
thank
challeng
#thank
#posit
chill
night
with
cream
grown
#chill
#biher
absolut
origin
hate
#bigotri
#altright
hatr
african
american
#potu
#theresist
sweet
#instagood
#idola
#idol
#followm
#selfi
these
tragedi
america
first
with
kill
#christinagrimmi
#orlando
#america
safe
place
t

take
anoth
day
golf
ever
sinc
zayn
left
they
never
been
same
happi
father
#lovey
#fathersday
#sunday
#father
#daddi
shock
monday
need
find
home
yeah
found
dream
cottag
tuesday
save
thousand
free
search
login
broker
#actor
#seeklearn
#stafresh
actual
order
kyli
hope
famili
made
arrang
make
sure
that
#bastard
access
#socialmedia
firm
build
nuclear
reactor
india
#smaphon
bull
will
domin
your
bull
will
direct
whatev
want
when
#lifeisbeauti
#loveit
#workhard
#trainhard
matter
where
#bless
#fitlif
oscar
tabarez
talk
lui
suarez
angri
reaction
#spo
#dure
#lui
#oscar
play
#njoyhit
hitmusicst
join
#nice
#nyc
onli
week
#personaltrain
full
time
will
have
slot
avail
from
june
spread
mother
take
care
children
sometim
children
cant
take
care
their
mother
thank
good
night
sleep
#thank
#posit
play
bride
nocturn
#melancholi
#melancholymus
#tvk
fathersday
father
tatay
daddi
enjoy
wath
voic
kid
thank
friend
#thank
#posit
thank
mason
jar
#thank
#posit
nigger
#lifelesson
white
grew
#blogpost
#whitepeopl
#re

similar
smoother
feel
great
kiki
felt
ignor
today
make
kiki
danc
again
#kikid
#miabbook
sourc
#inspir
ideal
#lyf
#baba
father
day
congrat
thoma
your
#beauti
home
tehaleh
welcom
lennar
famili
#homeown
miss
day
when
friend
play
xbox
case
scraggli
hair
love
dincwear
word
straight
saturday
#brickingit
bihday
sexi
girl
girl
boy
nake
onli
where
major
fan
like
salti
fan
just
need
someon
about
chang
daili
basi
week
until
handov
network
team
soon
then
when
thi
come
singapor
babi
sock
here
#shop
#cool
#home
#fun
like
video
from
#sjw
retard
want
more
wait
#doubledown
wife
#veganbeerfest
#vegan
lmfao
deadass
what
amaz
interview
#bjmckenzi
#born
#bjmuzic
boasti
tuesday
last
night
boom
boom
harri
hype
bihday
balayya
even
that
mass
look
craze
fan
screen
romanc
legend
#jaibalayya
woohoo
#kingsland
#highlandreserv
#hous
#famili
#build
#ourhom
outlin
theme
would
poem
haha
#decor
buffalo
simul
buffalo
take
vicin
their
home
thi
sold
paint
that
go
beauti
home
thi
week
#sold
#hope
#newyear
busi
#endof
#tedt

...

around
draghi
eye
#blog
#silver
#gold
#forex
belong
here
there
place
thi
world
#depress
#lone
#new
#followm
#feel
be
separ
#god
doe
mean
live
great
#fulfil
life
#die
live
#easter
#pstlovedayuyi
facebook
friend
enjoy
#avon
#freeshippng
#shop
happi
pitti
summer
#pitbul
#summer
#terrier
#pitbullmama
casa
dieter
save
date
sourcen
live
#thependulum
#newshow
#policebrut
broad
think
like
that
have
self
esteem
will
settl
anyth
#smallmind
happi
saturday
#saturday
weekend
forget
sign
your
#fundrais
pack
suppo
#jeansforgen
get
your
badli
didn
want
today
come
#day
amala
lunch
church
father
heafelt
condol
goe
famili
jazreel
remain
icon
african
music
circl
#ripojb
#ojbjezreel
done
#aflfreopow
when
sleep
alway
hear
#stonecold
#play
#music
#night
#alway
messi
#babylov
#lalov
#ootd
#ootdkid
#smile
#sundayvib
nomad
spo
club
will
never
ever
understand
ignor
stupid
some
peopl
peopl
rather
full
hate
instead
took
book
there
that
boom
#chuf
#waitedforev
#delight
#modernrenaiss
your
soul
rest
peac
much
hate
w

peac
achiev
much
someon
took
everyth
from
#ripchr
whatev
decid
make
sure
make
film
film
pleas
#bihday
bihday
#bday
lucki
#posit
#affirm
wear
white
feel
fresh
smoothen
tangent
#monday
#morn
clear
blue
#week
#zip
consol
fight
real
consol
choic
#funni
normal
thi
what
hell
go
with
thi
land
our
when
mother
get
murder
blog
follow
recent
discov
check
stuff
know
what
think
save
thousand
free
search
login
broker
#actor
#seeklearn
#stafresh
distanc
relationship
today
#gratitudebomb
goe
spread
#posit
#new
stori
news
today
likeeeeeeeeeeeeeeee
#fridayfeel
#feelingamaz
abov
#unconsciousgenderbia
workplac
unconsci
#sexi
wait
hear
innov
interest
idea
bring
back
#restorativejustic
good
best
#essentialoil
#anxieti
#healthi
#peac
#altwaystoh
#gloryisour
great
news
thi
morn
realli
strong
squad
creat
#media
#beauti
#qingdynasti
#leadership
#ecommerc
#autumn
#brunett
so
travel
time
last
night
wait
girl
boy
#gbtoangela
hawaii
countdown
day
#hilif
watch
solid
week
which
mean
will
internet
solid
week
know
wher

father
#eur
sell
extend
attack
handl
#blog
#silver
#gold
#forex
want
today
#over
feel
what
#shit
again
happi
bihday
#love
girl
#girl
#good
#goodday
#instacool
#instas
relax
piano
music
keep
your
#quiet
dure
#juli
#firework
final
found
second
dress
wed
yesterday
befor
comment
need
practic
#mistresslif
good
riddanc
#blacklivesmatt
that
even
spell
socialist
love
uneduc
think
peopl
they
rule
them
iron
abund
#posit
#affirm
time
concentr
edinburgh
youth
gaitherin
#picoftheday
photo
eilidh
steel
want
live
sydney
take
ferri
work
everi
lunch
street
perform
swim
bondi
beach
well
that
work
done
need
financ
meet
like
#number
#holiday
liter
week
just
ticket
will
summer
kanami
sorana
thank
veri
veri
veri
love
#famili
#love
silent
major
refus
paicip
poll
backlash
presenc
will
felt
elect
#fear
have
snapchat
#feelingfunni
#laughingmybuttoff
hellacopt
tremendo
#arf
#azkenarockfestiv
#rock
#conc
#music
#concieo
#peopl
aren
protest
#trump
becaus
#republican
they
becaus
trump
fuher
#rbnz
market
split
betwe

rock
year
ahead
amrita
bihday
#fun
with
mkayyyi
#rubytuesday
#makingmemori
#friend
#friendship
#goodlif
actor
anton
yelchin
dead
#imdb
#antonyelchin
#ripantonyelchin
just
ticket
juli
london
gonna
awesom
what
stupid
healess
backhand
compliment
yourself
fact
that
might
thi
weekend
make
extrem
happi
girl
#missedhim
true
#busymum
#bath
#love
#instagood
ladi
moe
mountain
sour
cream
quesadilla
that
feel
when
peopl
avoid
understand
#depress
#ihatelif
#wisdom
tree
life
those
fruit
keep
eat
proverb
hello
your
#tomahawk
steak
doesn
seem
stock
where
keep
get
told
onli
store
crash
bandicoot
head
playstat
remast
classic
ratchet
clank
crash
life
enjoy
when
perform
other
make
them
#smile
#peac
thier
#life
devot
care
critic
#obama
decis
#israel
sanction
against
#russiahack
#liber
will
consid
thi
gerard
be
happi
doesn
mean
everyth
perfect
mean
#quot
#thursdaythought
made
thi
chang
while
back
what
differ
made
#love
be
love
#life
govern
#anti
semit
definit
conflat
with
valid
critic
#israel
opendemocraci


(49159, 200)

In [141]:
pca = PCA(n_components=100)

wordvec_df= pd.DataFrame(pca.fit_transform(wordvec_df))


In [142]:
wordvec_df

0         1         2         3         4         5         6   \
0     -0.677884 -0.499256 -0.308687 -0.213616  0.219886  0.509645  0.347232   
1     -1.614371 -0.773906 -0.815373  0.773265  0.863203 -0.673149  0.451865   
2      0.653643 -1.319410  0.153189 -0.395784  2.075387  1.838215  1.364936   
3      0.791284 -0.567878  0.641662 -0.912581 -0.544477  0.469869  0.928186   
4      1.022509  0.003989 -1.705887  0.397403 -0.717298  0.140778 -1.266598   
...         ...       ...       ...       ...       ...       ...       ...   
49154  0.261318  2.062523 -2.431396 -0.120508  0.283760  0.133837 -0.972104   
49155  1.242238 -0.242962  0.378397 -1.014468 -0.061426 -0.404383 -0.549956   
49156 -0.990697  0.315798 -0.968722 -0.580404  0.406757 -0.347695 -0.309599   
49157  0.554388  0.921880 -0.749535  0.203081 -0.473358  1.632010 -1.590442   
49158  0.465390  0.815617  0.685000  0.310047  0.140526  0.036651  0.534014   

             7         8         9   ...        90        91        92  \
0      1.204900 -0.211398 -0.664023  ...  0.147789  0.055826  0.069140   
1      0.449428 -0.197868 -0.477746  ... -0.241169  0.027872 -0.095651   
2     -1.213580 -0.031751  1.943168  ... -0.137661 -0.009188  0.134584   
3      1.792673  0.736147  0.219764  ... -0.008885 -0.066020 -0.100280   
4     -1.230669  0.122717 -0.196599  ...  0.095364  0.074618 -0.022363   
...         ...       ...       ...  ...       ...       ...       ...   
49154 -0.698123 -1.032500 -0.442893  ... -0.076471  0.148955 -0.111159   
49155 -0.404566  0.384758  0.896142  ...  0.171403  0.019824  0.062076   
49156 -0.098799  0.034883 -0.251189  ...  0.214880 -0.154939  0.061459   
49157 -0.221323 -1.332710 -0.159016  ... -0.101275 -0.014237  0.040704   
49158 -0.651741 -1.313527  0.176456  ...  0.165011 -0.184394 -0.200768   

             93        94        95        96        97        98        99  
0     -0.200560  0.076338  0.054557 -0.114675  0.123949  0.169500  0.175744  
1      0.028837 -0.128698  0.000508  0.000768 -0.127155  0.132550  0.122982  
2     -0.163102  0.020577  0.102197 -0.023827 -0.016967 -0.088225  0.000625  
3      0.049415  0.088387 -0.047487 -0.034834 -0.081329  0.021924  0.007059  
4      0.141821  0.022017 -0.178886  0.096170 -0.096885  0.302178 -0.139128  
...         ...       ...       ...       ...       ...       ...       ...  
49154  0.264836  0.036504  0.178514 -0.116479  0.048198 -0.105107 -0.042600  
49155  0.053593 -0.028284 -0.152287 -0.162705  0.017537 -0.034485  0.121101  
49156  0.132913  0.015136  0.036377  0.011062 -0.082402  0.198988 -0.044687  
49157  0.050846 -0.136655 -0.073146  0.183059  0.165900 -0.077414  0.060898  
49158 -0.008378 -0.050810  0.215376 -0.051437  0.138003 -0.137551  0.061922  

[49159 rows x 100 columns]

In [143]:
train_w2v = wordvec_df.iloc[:31962,:]
test_w2v = wordvec_df.iloc[31962:,:]
X_train, X_test, y_train, y_test = train_test_split(train_w2v, train_df['label'], test_size = 0.3, random_state = 42)


In [144]:
X_train

0         1         2         3         4         5         6   \
9635   2.624471  0.515438  1.800957 -0.184322 -1.198392 -0.452818  0.453118   
2447  -1.425817  0.131880 -0.054169 -0.819912  0.194953 -0.509902  0.447440   
16134 -0.895838 -0.066948 -1.781111 -0.281235 -1.067865  1.038028  1.200023   
18393 -1.288601 -1.281243  0.065877  0.647713 -0.693582 -1.170216 -0.189773   
4420  -1.651794 -0.737453 -0.167830 -0.924818  0.579290 -0.999443  0.169399   
...         ...       ...       ...       ...       ...       ...       ...   
29802 -2.763674 -0.031150 -0.798788 -0.104614  0.175371 -0.457565 -0.295046   
5390  -1.170898 -0.256169 -0.027675  0.233430 -0.278790 -0.602448 -0.074522   
860   -1.641310  0.973872 -0.187289  0.595811 -0.512981 -0.156943 -0.323692   
15795 -0.689386  2.304424 -1.374506 -0.057139  0.836147 -0.545169 -0.537852   
23654 -1.644120 -1.265469 -0.996075 -0.581760 -0.191759 -0.829257 -0.377133   

             7         8         9   ...        90        91        92  \
9635   0.700896  0.400426 -0.154162  ...  0.194677  0.204498 -0.114047   
2447   0.118203  0.440137  0.508196  ... -0.061619  0.047405 -0.091043   
16134  0.055944  0.148142 -0.206074  ...  0.081520  0.022338  0.327732   
18393 -0.132409 -0.185229  0.015169  ... -0.054925 -0.233963 -0.176290   
4420   0.407224  0.014277  0.428667  ...  0.357414  0.016904  0.111214   
...         ...       ...       ...  ...       ...       ...       ...   
29802  0.781385  0.142495 -0.327256  ... -0.132608 -0.083215  0.001809   
5390   0.616711 -0.266523  0.218888  ...  0.351121 -0.013408 -0.001745   
860   -0.346099 -0.520941 -0.062794  ...  0.228214 -0.052347  0.164483   
15795 -0.687897  0.049773  0.134791  ...  0.012843  0.057784 -0.089153   
23654 -0.681605  0.161195  0.507989  ... -0.193995  0.016481 -0.012018   

             93        94        95        96        97        98        99  
9635  -0.104857  0.120103  0.108788 -0.284608  0.187155 -0.007189 -0.020232  
2447  -0.097166 -0.144940  0.046481  0.099213  0.022232  0.028566  0.136228  
16134 -0.098200  0.177483  0.155703 -0.047467  0.007614 -0.046179 -0.016285  
18393  0.235625  0.062317 -0.057375  0.230426  0.104936 -0.215354  0.118304  
4420  -0.306066  0.096932  0.217834 -0.063292  0.069188 -0.055865 -0.123626  
...         ...       ...       ...       ...       ...       ...       ...  
29802 -0.347652 -0.139502 -0.114514  0.026203 -0.040509 -0.180906  0.085344  
5390  -0.080670 -0.123750  0.142726  0.087927 -0.118625 -0.125457  0.027042  
860   -0.088847  0.128110  0.050617 -0.068597 -0.022726 -0.192626  0.134176  
15795 -0.068592 -0.158665 -0.050465  0.024583 -0.138730 -0.064325 -0.075784  
23654 -0.057830 -0.165162 -0.065311 -0.064643 -0.072617 -0.131556 -0.010402  

[22373 rows x 100 columns]

In [145]:
X_test

0         1         2         3         4         5         6   \
12227  0.984952 -1.538475  0.178881 -0.387026  0.271838 -0.395183  0.021608   
14709  0.305437  0.689955  1.408575  0.512034 -0.169199  0.247145  0.179962   
19319 -1.707306  1.580756 -2.173951 -0.558489  0.778821 -0.608527 -0.513854   
4308   0.123531 -0.681615  0.196721 -0.377531 -0.496429 -0.852669 -0.216090   
24055  1.268794 -1.415189 -0.403975 -1.603548  1.728530  0.072602 -1.771389   
...         ...       ...       ...       ...       ...       ...       ...   
20593  0.791284 -0.567878  0.641662 -0.912581 -0.544477  0.469869  0.928186   
11682 -2.391515  0.377402 -0.863177 -0.116135 -0.483605 -0.522086 -0.996034   
10882  0.561941  1.612959  1.833655  1.187548 -0.427932  0.984477 -0.588371   
6084  -2.208453 -0.129749 -0.409416 -0.180105  0.130769 -0.188317  0.370011   
6952   0.859873  1.020531 -0.537395 -0.606410  0.003011  0.158616  0.057793   

             7         8         9   ...        90        91        92  \
12227 -0.713535  0.524769 -0.581301  ...  0.124319  0.258219 -0.166865   
14709  0.546242  0.441215 -0.361341  ... -0.031853  0.110873  0.202850   
19319  0.808866  0.085848 -0.040233  ...  0.098727 -0.061685 -0.043251   
4308  -1.197750 -0.864438 -0.081449  ... -0.013508 -0.106683 -0.020940   
24055 -0.435740 -0.299413 -1.841869  ... -0.057123  0.216219  0.150356   
...         ...       ...       ...  ...       ...       ...       ...   
20593  1.792673  0.736147  0.219764  ... -0.008885 -0.066020 -0.100280   
11682 -0.502672 -0.189229  0.132750  ... -0.103468 -0.110894 -0.063234   
10882 -0.193377  0.132641  0.150083  ...  0.080211 -0.158082  0.129190   
6084   0.280404  0.986670 -0.778992  ... -0.117519  0.008992 -0.097046   
6952   0.537071  0.303263  0.330476  ... -0.079137 -0.247031  0.007474   

             93        94        95        96        97        98        99  
12227 -0.214979 -0.036177  0.230935 -0.233920 -0.013472 -0.149751  0.076987  
14709 -0.079183  0.014259  0.054475  0.084924 -0.020628 -0.234618  0.014766  
19319 -0.139932 -0.078410  0.093642  0.161745  0.076146  0.261137 -0.070237  
4308   0.246513 -0.062116  0.060035 -0.166324  0.194659  0.252828 -0.140482  
24055  0.081067  0.093039  0.099288  0.245049 -0.027623 -0.222531  0.014611  
...         ...       ...       ...       ...       ...       ...       ...  
20593  0.049415  0.088387 -0.047487 -0.034834 -0.081329  0.021924  0.007059  
11682 -0.304029 -0.142730  0.270902 -0.051037 -0.234472  0.066316  0.140482  
10882 -0.054010 -0.016348  0.052992  0.169181 -0.098111 -0.153806  0.113255  
6084  -0.267952 -0.160240 -0.075655  0.013617  0.060071  0.090722  0.067694  
6952   0.117141  0.137894 -0.151711 -0.055974  0.135998  0.133627  0.040063  

[9589 rows x 100 columns]

In [146]:
y_train

9635     0
2447     0
16134    0
18393    0
4420     0
        ..
29802    0
5390     0
860      1
15795    0
23654    0
Name: label, Length: 22373, dtype: int64

In [147]:
from sklearn.linear_model import LogisticRegression
clss = LogisticRegression(random_state = 42)
clss.fit(X_train, y_train)
print(clss.score(X_test,y_test))
# Predicting the Test set results
y_pred = clss.predict(X_test)

y_pred 


0.9446240483887788


array([0, 0, 1, ..., 0, 0, 0], dtype=int64)

In [148]:
from sklearn.metrics import confusion_matrix,accuracy_score
cm = confusion_matrix(y_test, y_pred)

AccScore = accuracy_score(y_test, y_pred, normalize=False)
print('Accuracy Score is : ', AccScore)

cm

Accuracy Score is :  9058


array([[8806,   99],
       [ 432,  252]], dtype=int64)

In [149]:

from sklearn.metrics import mean_absolute_error
mean_absolute_error(y_test, y_pred)

# from sklearn.metrics import mean_squared_error
# mean_squared_error(y_test, y_pred)

# from sklearn.metrics import median_absolute_error
# median_absolute_error(y_test, y_pred)

0.05537595161122119

In [150]:
test_w2v

0         1         2         3         4         5         6   \
31962  1.396116 -0.301479 -0.866473 -0.258954 -0.571608  0.386932 -0.326101   
31963  1.125881  0.395390 -0.168882 -0.728731  0.187735 -0.984741  0.334247   
31964  0.694074 -0.826271 -3.473908  0.094568 -3.210079  4.153528 -0.185136   
31965 -1.036592  0.525145  0.375631 -0.121982  0.042914 -0.170463  0.652244   
31966  0.896549 -0.557012  0.989193 -0.269429  1.070155  0.444806  0.783926   
...         ...       ...       ...       ...       ...       ...       ...   
49154  0.261318  2.062523 -2.431396 -0.120508  0.283760  0.133837 -0.972104   
49155  1.242238 -0.242962  0.378397 -1.014468 -0.061426 -0.404383 -0.549956   
49156 -0.990697  0.315798 -0.968722 -0.580404  0.406757 -0.347695 -0.309599   
49157  0.554388  0.921880 -0.749535  0.203081 -0.473358  1.632010 -1.590442   
49158  0.465390  0.815617  0.685000  0.310047  0.140526  0.036651  0.534014   

             7         8         9   ...        90        91        92  \
31962 -0.055057 -0.343053  0.423325  ... -0.076761 -0.283530 -0.254431   
31963 -0.397892 -1.061239 -0.762451  ... -0.155986 -0.039783  0.162201   
31964  0.695202 -1.585353  0.562157  ...  0.029340  0.079359 -0.072815   
31965  0.314093 -0.057181 -0.010481  ...  0.111292  0.002374  0.191191   
31966  0.427684 -0.262405  0.681304  ...  0.117732  0.167628 -0.010797   
...         ...       ...       ...  ...       ...       ...       ...   
49154 -0.698123 -1.032500 -0.442893  ... -0.076471  0.148955 -0.111159   
49155 -0.404566  0.384758  0.896142  ...  0.171403  0.019824  0.062076   
49156 -0.098799  0.034883 -0.251189  ...  0.214880 -0.154939  0.061459   
49157 -0.221323 -1.332710 -0.159016  ... -0.101275 -0.014237  0.040704   
49158 -0.651741 -1.313527  0.176456  ...  0.165011 -0.184394 -0.200768   

             93        94        95        96        97        98        99  
31962 -0.022711 -0.142445 -0.170752 -0.123145 -0.199756 -0.199600 -0.231481  
31963 -0.027161  0.136152 -0.159831  0.025129  0.006916 -0.103948  0.054109  
31964 -0.071113  0.001653 -0.128344  0.048573 -0.018176  0.012143 -0.037160  
31965  0.094651  0.098447 -0.120032 -0.085401  0.014810  0.254554  0.165221  
31966  0.002635  0.011717  0.240425  0.061405 -0.093277  0.014612  0.084295  
...         ...       ...       ...       ...       ...       ...       ...  
49154  0.264836  0.036504  0.178514 -0.116479  0.048198 -0.105107 -0.042600  
49155  0.053593 -0.028284 -0.152287 -0.162705  0.017537 -0.034485  0.121101  
49156  0.132913  0.015136  0.036377  0.011062 -0.082402  0.198988 -0.044687  
49157  0.050846 -0.136655 -0.073146  0.183059  0.165900 -0.077414  0.060898  
49158 -0.008378 -0.050810  0.215376 -0.051437  0.138003 -0.137551  0.061922  

[17197 rows x 100 columns]

In [151]:
test_pred=clss.predict(test_w2v)
test_pred = [0 if i<0.5 else 1 for i in test_pred]

In [152]:
test_df['label']=test_pred

In [153]:
test_df['label'].value_counts()

0    16537
1      660
Name: label, dtype: int64

In [154]:
test_df

id                                              tweet  label
0      31963  #studiolife #aislife #requires #passion #dedic...      0
1      31964   @user #white #supremacists want everyone to s...      0
2      31965  safe ways to heal your #acne!!    #altwaystohe...      0
3      31966  is the hp and the cursed child book up for res...      0
4      31967    3rd #bihday to my amazing, hilarious #nephew...      0
...      ...                                                ...    ...
17192  49155  thought factory: left-right polarisation! #tru...      1
17193  49156  feeling like a mermaid ð #hairflip #neverre...      0
17194  49157  #hillary #campaigned today in #ohio((omg)) &am...      0
17195  49158  happy, at work conference: right mindset leads...      0
17196  49159  my   song "so glad" free download!  #shoegaze ...      0

[17197 rows x 3 columns]

In [155]:
from sklearn.svm import SVC

In [156]:

svc = SVC()
svc.fit(X_train, y_train
       )

sc = svc.score(X_test,y_test)

print('score = ' , sc)

score =  0.947752633225571


In [157]:
test_pred=svc.predict(test_w2v)
test_pred = [0 if i<0.5 else 1 for i in test_pred]

In [158]:
test_df['label']=test_pred

In [159]:
test_df['label'].value_counts()

0    16624
1      573
Name: label, dtype: int64

In [160]:
from sklearn.tree import DecisionTreeClassifier

In [161]:

clf_gini = DecisionTreeClassifier(criterion = "gini", random_state = 100,max_depth=4, min_samples_leaf=5)
clf_gini.fit(X_train, y_train)

clf_entropy = DecisionTreeClassifier(criterion = "entropy", random_state = 100,max_depth=5, min_samples_leaf=5)
clf_entropy.fit(X_train, y_train)

DecisionTreeClassifier(criterion='entropy', max_depth=5, min_samples_leaf=5,
                       random_state=100)

In [162]:


y_pred = clf_gini.predict(X_test)
y_pred

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [163]:

y_pred_en = clf_entropy.predict(X_test)
y_pred_en

print ("Accuracy for gini is ", accuracy_score(y_test,y_pred)*100)

print ("Accuracy for entropy is ", accuracy_score(y_test,y_pred_en)*100)

Accuracy for gini is  92.86682657211388
Accuracy for entropy is  92.83554072374596


In [164]:
# the best score is svc
submission = test_df[['id','label']]
submission.to_csv('model_result.csv', index=False)